# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it.

You will find more info about virtual environments in the course content and on the web.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [51]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.onrender.com/"

# assign the /status endpoint to another variable called status_url (1 line)
status_url = "https://country-leaders.onrender.com/status"
# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(status_url)

# check the status_code using a condition and print appropriate messages (4 lines)
if req.status_code == 200:
    print("200, OK")
else:
    print("Not ok")

200, OK


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [52]:
# Set the countries_url variable (1 line)
countries_url = "https://country-leaders.onrender.com/countries"

# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(countries_url)

# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()

# display the request's status code and the countries variable (1 line)
print(req.status_code)
print(countries)

403
{'message': 'The cookie is missing'}


### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [53]:
# Set the cookie_url variable (1 line)
cookie_url = "https://country-leaders.onrender.com/cookie"

# Query the enpoint, set the cookies variable and display it (2 lines)
req = requests.get(cookie_url)
cookies = req.cookies
print(cookies)

<RequestsCookieJar[<Cookie user_cookie=e6ba8867-b8c2-45b7-b65e-21825449324a for country-leaders.onrender.com/>]>


Try to query the countries endpoint using the cookie, save the output and print it.

In [54]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = requests.get(countries_url, cookies=cookies)

# display the countries variable (1 line)
print(countries)

<Response [200]>


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [55]:
# Set the leaders_url variable (1 line)
leaders_url = root_url + "leaders"

# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url)

# display the leaders variable (1 line)
print(leaders.text)
print(leaders.status_code)

{"message":"The cookie is missing"}
403


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [56]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)

params = {
    "country": "us"
}
leaders = requests.get(leaders_url, cookies=cookies, params=params)

# assign the output to the leaders variable (1 line)
print(leaders)
# display the leaders variable (1 line)
print(leaders.text)

<Response [200]>
[{"id":"Q23","first_name":"George","last_name":"Washington","birth_date":"1732-02-22","death_date":"1799-12-14","place_of_birth":"Westmoreland County","wikipedia_url":"https://en.wikipedia.org/wiki/George_Washington","start_mandate":"1789-04-30","end_mandate":"1797-03-04"},{"id":"Q76","first_name":"Barack","last_name":"Obama","birth_date":"1961-08-04","death_date":null,"place_of_birth":"Kapiolani Medical Center for Women and Children","wikipedia_url":"https://en.wikipedia.org/wiki/Barack_Obama","start_mandate":"2009-01-20","end_mandate":"2017-01-20"},{"id":"Q91","first_name":"Abraham","last_name":"Lincoln","birth_date":"1809-02-12","death_date":"1865-04-15","place_of_birth":"Sinking Spring Farm","wikipedia_url":"https://en.wikipedia.org/wiki/Abraham_Lincoln","start_mandate":"1861-03-04","end_mandate":"1865-04-15"},{"id":"Q207","first_name":"George","last_name":"Bush","birth_date":"1946-07-06","death_date":null,"place_of_birth":"New Haven","wikipedia_url":"https://en.wi

### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [57]:
countries_list = countries.json()
countries_list

['us', 'be', 'ma', 'ru', 'fr']

In [58]:
# 4 lines
leaders_per_country = {}
for country in countries_list:
    params = { "country": country}
    leaders = requests.get(leaders_url, cookies=cookies, params=params)
    leaders_per_country[country]= leaders.json()
leaders_per_country

{'us': [{'id': 'Q23',
   'first_name': 'George',
   'last_name': 'Washington',
   'birth_date': '1732-02-22',
   'death_date': '1799-12-14',
   'place_of_birth': 'Westmoreland County',
   'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington',
   'start_mandate': '1789-04-30',
   'end_mandate': '1797-03-04'},
  {'id': 'Q76',
   'first_name': 'Barack',
   'last_name': 'Obama',
   'birth_date': '1961-08-04',
   'death_date': None,
   'place_of_birth': 'Kapiolani Medical Center for Women and Children',
   'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama',
   'start_mandate': '2009-01-20',
   'end_mandate': '2017-01-20'},
  {'id': 'Q91',
   'first_name': 'Abraham',
   'last_name': 'Lincoln',
   'birth_date': '1809-02-12',
   'death_date': '1865-04-15',
   'place_of_birth': 'Sinking Spring Farm',
   'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln',
   'start_mandate': '1861-03-04',
   'end_mandate': '1865-04-15'},
  {'id': 'Q207',
   'first_name': 'Ge

In [59]:
# or 1 line


It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [60]:
# < 15 lines
def get_leaders():
    dict_leaders = {}
    for country in countries_list:
        params = { "country": country}
        leaders = requests.get(leaders_url, cookies=cookies, params=params)
        dict_leaders[country]= leaders.json()
    return dict_leaders

In [61]:
params = {
    "country": "ma"
}
leaders_ma = requests.get(leaders_url, cookies=cookies, params=params)
leaders_ma.json()

[{'id': 'Q57553',
  'first_name': 'Mohammed',
  'last_name': 'None',
  'birth_date': '1963-08-21',
  'death_date': None,
  'place_of_birth': 'Rabat',
  'wikipedia_url': 'https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%B3%D8%A7%D8%AF%D8%B3_%D8%A8%D9%86_%D8%A7%D9%84%D8%AD%D8%B3%D9%86',
  'start_mandate': '1999-07-23',
  'end_mandate': None},
 {'id': 'Q69103',
  'first_name': 'Hassan',
  'last_name': 'None',
  'birth_date': '1929-07-09',
  'death_date': '1999-07-20',
  'place_of_birth': 'Rabat',
  'wikipedia_url': 'https://ar.wikipedia.org/wiki/%D8%A7%D9%84%D8%AD%D8%B3%D9%86_%D8%A7%D9%84%D8%AB%D8%A7%D9%86%D9%8A_%D8%A8%D9%86_%D9%85%D8%AD%D9%85%D8%AF',
  'start_mandate': '1961-02-26',
  'end_mandate': '1999-07-23'},
 {'id': 'Q193874',
  'first_name': 'Mohammed',
  'last_name': 'None',
  'birth_date': '1909-08-10',
  'death_date': '1961-02-26',
  'place_of_birth': 'Fez',
  'wikipedia_url': 'https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%AE%D8%A7

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [62]:
# 2 lines
leaders_per_country = get_leaders()
leaders_per_country


{'us': [{'id': 'Q23',
   'first_name': 'George',
   'last_name': 'Washington',
   'birth_date': '1732-02-22',
   'death_date': '1799-12-14',
   'place_of_birth': 'Westmoreland County',
   'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington',
   'start_mandate': '1789-04-30',
   'end_mandate': '1797-03-04'},
  {'id': 'Q76',
   'first_name': 'Barack',
   'last_name': 'Obama',
   'birth_date': '1961-08-04',
   'death_date': None,
   'place_of_birth': 'Kapiolani Medical Center for Women and Children',
   'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama',
   'start_mandate': '2009-01-20',
   'end_mandate': '2017-01-20'},
  {'id': 'Q91',
   'first_name': 'Abraham',
   'last_name': 'Lincoln',
   'birth_date': '1809-02-12',
   'death_date': '1865-04-15',
   'place_of_birth': 'Sinking Spring Farm',
   'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln',
   'start_mandate': '1861-03-04',
   'end_mandate': '1865-04-15'},
  {'id': 'Q207',
   'first_name': 'Ge

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [63]:
# 3 lines
r_GW = requests.get("https://en.wikipedia.org/wiki/George_Washington")
print(r_GW.text)


<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" lang="en" dir="ltr">
<head>
<meta charset="UTF-8">
<title>George Washington - Wikipedia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [64]:
# 3 lines
from bs4 import BeautifulSoup
html_content = BeautifulSoup(r_GW.text, 'html.parser')
print(html_content.get_text())





George Washington - Wikipedia



































Jump to content







Main menu





Main menu
move to sidebar
hide



		Navigation
	


Main pageContentsCurrent eventsRandom articleAbout WikipediaContact us





		Contribute
	


HelpLearn to editCommunity portalRecent changesUpload file



















Search











Search






















Appearance
















Donate

Create account

Log in








Personal tools





Donate Create account Log in





		Pages for logged out editors learn more



ContributionsTalk




























Contents
move to sidebar
hide




(Top)





1
Early life (1732–1752)








2
Colonial military career (1752–1758)




Toggle Colonial military career (1752–1758) subsection





2.1
French and Indian War










3
Marriage, civilian, and political life (1755–1775)




Toggle Marriage, civilian, and political life (1755–1775) subsection





3.1
Opposition to the British Parliament and Crown










4
Co

In [65]:
print(html_content.prettify())

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   George Washington - Wikipedia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [66]:
# 2 lines
paragraphs = html_content.find_all('p')
paragraphs

[<p class="mw-empty-elt">
 </p>,
 <p><b>George Washington</b> (February 22, 1732 – <span class="nowrap">December 14</span>, 1799) was a <a class="mw-redirect" href="/wiki/Founding_Father_of_the_United_States" title="Founding Father of the United States">Founding Father of the United States</a>, military officer, and farmer who served as the first <a href="/wiki/President_of_the_United_States" title="President of the United States">president of the United States</a> from 1789 to 1797. Appointed by the <a href="/wiki/Second_Continental_Congress" title="Second Continental Congress">Second Continental Congress</a> as commander of the <a href="/wiki/Continental_Army" title="Continental Army">Continental Army</a> in 1775, Washington led <a href="/wiki/Patriot_(American_Revolution)" title="Patriot (American Revolution)">Patriot</a> forces to victory in the <a href="/wiki/American_Revolutionary_War" title="American Revolutionary War">American Revolutionary War</a> and then served as president 

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [67]:
html_content.p.get_text()

'\n'

In [68]:
# <10 lines
name = html_content.find("h1").text
for p in paragraphs:
    if p.get_text().startswith(name):
        print(p.get_text())
        break



George Washington (February 22, 1732 – December 14, 1799) was a Founding Father of the United States, military officer, and farmer who served as the first president of the United States from 1789 to 1797. Appointed by the Second Continental Congress as commander of the Continental Army in 1775, Washington led Patriot forces to victory in the American Revolutionary War and then served as president of the Constitutional Convention in 1787, which drafted the current Constitution of the United States. Washington has thus become commonly known as the "Father of his Country".



At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [69]:
# 10 lines
def get_first_paragraph(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    wiki_content = requests.get(wikipedia_url)
    html_content = BeautifulSoup(wiki_content.text, 'html.parser')
    name = html_content.find("h1").text[0]
    paragraphs = html_content.find_all('p')
    for p in paragraphs:
        #if p.get_text().startswith(name):
        if p.get_text().__contains__(name):
            first_paragraph = p.get_text()
            return first_paragraph

In [70]:
# Test: 3 lines
#FR
print(get_first_paragraph("https://fr.wikipedia.org/wiki/Emmanuel_Macron"))

#US
print(get_first_paragraph("https://en.wikipedia.org/wiki/Abraham_Lincoln"))

#US
print(get_first_paragraph("https://en.wikipedia.org/wiki/Barack_Obama"))

#BE
print(get_first_paragraph("https://nl.wikipedia.org/wiki/Guy_Verhofstadt"))

#MA
print(get_first_paragraph("https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%AE%D8%A7%D9%85%D8%B3_%D8%A8%D9%86_%D9%8A%D9%88%D8%B3%D9%81"))

#RU
print(get_first_paragraph("https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87"))

https://fr.wikipedia.org/wiki/Emmanuel_Macron
Emmanuel Macron ([ɛmanɥɛl makʁɔ̃][e] Écouter), né le 21 décembre 1977 à Amiens (Somme), est un haut fonctionnaire, banquier d'affaires et homme d'État français. Il est Président de la République française depuis le 14 mai 2017.

https://en.wikipedia.org/wiki/Abraham_Lincoln
Abraham Lincoln (/ˈlɪŋkən/ LINK-ən; February 12, 1809 – April 15, 1865) was the 16th president of the United States, serving from 1861 until his assassination in 1865. He led the United States through the American Civil War, defending the nation as a constitutional union, defeating the Confederacy, playing a major role in the abolition of slavery, expanding the power of the federal government, and modernizing the U.S. economy.

https://en.wikipedia.org/wiki/Barack_Obama
Barack Hussein Obama II[a] (born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. As a member of the Democratic Party, he was the first Af

### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [71]:
# 3 lines
# remove references [number/letter] 
# remove phonetic pronunciation
# examples :  ([ɛmanɥɛl makʁɔ̃][e] Écouter), /ˈlɪŋkən/ LINK-ən;
# remove html code --> I don't see any

import re
first_paragraph = "Guy Maurice Marie-Louise Verhofstadt[5] (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.[6]"
first_paragraph = re.sub(r"\[\d+\]", "", first_paragraph)
first_paragraph

'Guy Maurice Marie-Louise Verhofstadt (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.'

Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [72]:
# 10 lines
def get_first_paragraph(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    wiki_content = requests.get(wikipedia_url)
    html_content = BeautifulSoup(wiki_content.text, 'html.parser')
    name = html_content.find("h1").text[0]
    paragraphs = html_content.find_all('p')
    for p in paragraphs:
        #if p.get_text().startswith(name):
        if p.get_text().__contains__(name):
            first_paragraph = p.get_text()
            first_paragraph = re.sub(r"\[\d+\]", "", first_paragraph)
            first_paragraph = re.sub(r"\[\w+\]", "", first_paragraph)
            first_paragraph = re.sub(r"\[.+\]", "", first_paragraph)
            print(first_paragraph)
            break

In [73]:
#FR
get_first_paragraph("https://fr.wikipedia.org/wiki/Emmanuel_Macron")

#US
get_first_paragraph("https://en.wikipedia.org/wiki/Abraham_Lincoln")

#US
get_first_paragraph("https://en.wikipedia.org/wiki/Barack_Obama")

#BE
get_first_paragraph("https://nl.wikipedia.org/wiki/Guy_Verhofstadt")

#MA
get_first_paragraph("https://ar.wikipedia.org/wiki/%D9%85%D8%AD%D9%85%D8%AF_%D8%A7%D9%84%D8%AE%D8%A7%D9%85%D8%B3_%D8%A8%D9%86_%D9%8A%D9%88%D8%B3%D9%81")

#RU
get_first_paragraph("https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87")

https://fr.wikipedia.org/wiki/Emmanuel_Macron
Emmanuel Macron ( Écouter), né le 21 décembre 1977 à Amiens (Somme), est un haut fonctionnaire, banquier d'affaires et homme d'État français. Il est Président de la République française depuis le 14 mai 2017.

https://en.wikipedia.org/wiki/Abraham_Lincoln
Abraham Lincoln (/ˈlɪŋkən/ LINK-ən; February 12, 1809 – April 15, 1865) was the 16th president of the United States, serving from 1861 until his assassination in 1865. He led the United States through the American Civil War, defending the nation as a constitutional union, defeating the Confederacy, playing a major role in the abolition of slavery, expanding the power of the federal government, and modernizing the U.S. economy.

https://en.wikipedia.org/wiki/Barack_Obama
Barack Hussein Obama II (born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. As a member of the Democratic Party, he was the first African-American preside

Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [74]:
# < 20 lines
first_paragraph = "<b>Guy Maurice Marie-Louise Verhofstadt</b> (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.[6]"
first_paragraph = re.sub("<[^>]*>", " ", first_paragraph)
first_paragraph
# to remove HTML tags : re.sub("<[^>]*>", "", first_paragraph)


' Guy Maurice Marie-Louise Verhofstadt  (uitspraakⓘ) (Dendermonde, 11 april 1953) is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten (Open Vld). Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa (ALDE) was.[6]'

## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [75]:
# < 20 lines
def get_leaders():
    dict_leaders = {}
    for country in countries_list:
        params = { "country": country}
        leaders = requests.get(leaders_url, cookies=cookies, params=params)
        dict_leaders[country]= leaders.json()
        for elem in dict_leaders[country]:
            get_first_paragraph(elem["wikipedia_url"])

In [76]:
# Check the output of your function (2 lines)

get_leaders()

https://en.wikipedia.org/wiki/George_Washington
George Washington (February 22, 1732 – December 14, 1799) was a Founding Father of the United States, military officer, and farmer who served as the first president of the United States from 1789 to 1797. Appointed by the Second Continental Congress as commander of the Continental Army in 1775, Washington led Patriot forces to victory in the American Revolutionary War and then served as president of the Constitutional Convention in 1787, which drafted the current Constitution of the United States. Washington has thus become commonly known as the "Father of his Country".

https://en.wikipedia.org/wiki/Barack_Obama
Barack Hussein Obama II (born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. As a member of the Democratic Party, he was the first African-American president in U.S. history. Obama previously served as a U.S. senator representing Illinois from 2005 to 2008 and as

TypeError: string indices must be integers, not 'str'

Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [77]:
# < 25 lines

# Set the cookie_url variable (1 line)
cookie_url = "https://country-leaders.onrender.com/cookie"

# Query the enpoint, set the cookies variable and display it (2 lines)
req = requests.get(cookie_url)
cookies = req.cookies

def get_leaders():
    dict_leaders = {}
    for country in countries_list:
        params = { "country": country}
        try:
            leaders = requests.get(leaders_url, cookies=cookies, params=params)
            dict_leaders[country]= leaders.json()
            for elem in dict_leaders[country]:
                get_first_paragraph(elem["wikipedia_url"])
        except:
            cookie_url = "https://country-leaders.onrender.com/cookie"
            # Query the enpoint, set the cookies variable and display it (2 lines)
            req = requests.get(cookie_url)
            cookies = req.cookies
            leaders = requests.get(leaders_url, cookies=cookies, params=params)
            dict_leaders[country]= leaders.json()
            for elem in dict_leaders[country]:
                get_first_paragraph(elem["wikipedia_url"])


Check the output of your function again.

In [78]:
# Check the output of your function (1 line)
get_leaders()

https://en.wikipedia.org/wiki/George_Washington
George Washington (February 22, 1732 – December 14, 1799) was a Founding Father of the United States, military officer, and farmer who served as the first president of the United States from 1789 to 1797. Appointed by the Second Continental Congress as commander of the Continental Army in 1775, Washington led Patriot forces to victory in the American Revolutionary War and then served as president of the Constitutional Convention in 1787, which drafted the current Constitution of the United States. Washington has thus become commonly known as the "Father of his Country".

https://en.wikipedia.org/wiki/Barack_Obama
Barack Hussein Obama II (born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. As a member of the Democratic Party, he was the first African-American president in U.S. history. Obama previously served as a U.S. senator representing Illinois from 2005 to 2008 and as

Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [79]:
# < 20 lines
from requests import Session

cookie_url = "https://country-leaders.onrender.com/cookie"
req = requests.get(cookie_url)
cookies = req.cookies


def get_first_paragraph(wikipedia_url, session: Session):
    print(wikipedia_url) # keep this for the rest of the notebook
    wiki_content = session.get(wikipedia_url)
    html_content = BeautifulSoup(wiki_content.text, 'html.parser')
    name = html_content.find("h1").text[0]
    paragraphs = html_content.find_all('p')
    for p in paragraphs:
        #if p.get_text().startswith(name):
        if p.get_text().__contains__(name):
            first_paragraph = p.get_text()
            first_paragraph = re.sub(r"\[\d+\]", "", first_paragraph)
            first_paragraph = re.sub(r"\[\w+\]", "", first_paragraph)
            first_paragraph = re.sub(r"\[.+\]", "", first_paragraph)
            print(first_paragraph)
            break






Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [86]:
# <25 lines
def get_leaders():
    with Session() as session:
        dict_leaders = {}
        for country in countries_list:
            params = { "country": country}
            try:
                leaders = requests.get(leaders_url, cookies=cookies, params=params)
                dict_leaders[country]= leaders.json()
                for elem in dict_leaders[country]:
                    get_first_paragraph(elem["wikipedia_url"], session)
            except:
                cookie_url = "https://country-leaders.onrender.com/cookie"
                # Query the enpoint, set the cookies variable and display it (2 lines)
                req = requests.get(cookie_url)
                cookies = req.cookies
                leaders = requests.get(leaders_url, cookies=cookies, params=params)
                dict_leaders[country]= leaders.json()
                for elem in dict_leaders[country]:
                    get_first_paragraph(elem["wikipedia_url"], session)
    return dict_leaders



Test your new functions.



In [87]:
leaders_per_country = get_leaders()

https://en.wikipedia.org/wiki/George_Washington
George Washington (February 22, 1732 – December 14, 1799) was a Founding Father of the United States, military officer, and farmer who served as the first president of the United States from 1789 to 1797. Appointed by the Second Continental Congress as commander of the Continental Army in 1775, Washington led Patriot forces to victory in the American Revolutionary War and then served as president of the Constitutional Convention in 1787, which drafted the current Constitution of the United States. Washington has thus become commonly known as the "Father of his Country".

https://en.wikipedia.org/wiki/Barack_Obama
Barack Hussein Obama II (born August 4, 1961) is an American politician who served as the 44th president of the United States from 2009 to 2017. As a member of the Democratic Party, he was the first African-American president in U.S. history. Obama previously served as a U.S. senator representing Illinois from 2005 to 2008 and as

## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [ ]:
# 3 lines
import json
with open("leaders.json", "w") as outfile: 
    json.dump(leaders_per_country, outfile)

    

Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [ ]:
# 3 lines
with open("leaders.json", "r") as file:
    leaders_json = json.load(file)

# Print the data
print(leaders_json)


{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

Make a function `save(leaders_per_country)` to call this code easily.

In [ ]:
# 3 lines
def save(json_filename):
    with open("leaders.json", "w") as outfile: 
        json.dump(json_filename, outfile)

save(leaders_per_country)

## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!